In [1]:
#https://plot.ly/python/3d-network-graph/
import igraph as ig

In [2]:
import json
#import urllib
import requests

In [3]:
#import plotly.plotly as py
#import plotly.graph_objs as go

In [4]:
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
print(__version__) # requires version >= 1.9.0
import plotly.graph_objs as go
init_notebook_mode(connected=True)

3.1.1


## data

In [5]:
#resp = requests.get(les_miz_link)
#data = resp.json()
#data.keys()


In [6]:
with open("data/les_miz.json", 'r') as f:
    data = json.loads(f.read())

In [7]:
N=len(data['nodes'])
N

77

In [8]:
#with open("data/les_miz.json", 'w') as f:
#    f.write(json.dumps(data))

## starting igraph setup

In [9]:
L=len(data['links'])
Edges=[(data['links'][k]['source'], data['links'][k]['target']) for k in range(L)]

G=ig.Graph(Edges, directed=False)

In [10]:
data['nodes'][0]

{'group': 1, 'name': 'Myriel'}

In [11]:
labels=[]
group=[]
for node in data['nodes']:
    labels.append(node['name'])
    group.append(node['group'])

In [12]:
layt=G.layout('kk', dim=3) 

In [13]:
layt[5]

[-6.734579021483016, -0.9955865027703368, 4.402942241915864]

In [14]:
Xn=[layt[k][0] for k in range(N)]# x-coordinates of nodes
Yn=[layt[k][1] for k in range(N)]# y-coordinates
Zn=[layt[k][2] for k in range(N)]# z-coordinates
Xe=[]
Ye=[]
Ze=[]
for e in Edges:
    Xe+=[layt[e[0]][0],layt[e[1]][0], None]# x-coordinates of edge ends
    Ye+=[layt[e[0]][1],layt[e[1]][1], None]  
    Ze+=[layt[e[0]][2],layt[e[1]][2], None] 

## plotly

In [15]:

trace1=go.Scatter3d(x=Xe,
               y=Ye,
               z=Ze,
               mode='lines',
               line=dict(color='rgb(125,125,125)', width=1),
               hoverinfo='none'
               )

trace2=go.Scatter3d(x=Xn,
               y=Yn,
               z=Zn,
               mode='markers',
               name='actors',
               marker=dict(symbol='circle',
                             size=6,
                             color=group,
                             colorscale='Viridis',
                             line=dict(color='rgb(50,50,50)', width=0.5)
                             ),
               text=labels,
               hoverinfo='text'
               )

axis=dict(showbackground=False,
          showline=False,
          zeroline=False,
          showgrid=False,
          showticklabels=False,
          title=''
          )

layout = go.Layout(
         title="Network of coappearances of characters in Victor Hugo's novel<br> Les Miserables (3D visualization)",
         width=1000,
         height=1000,
         showlegend=False,
         scene=dict(
             xaxis=dict(axis),
             yaxis=dict(axis),
             zaxis=dict(axis),
        ),
     margin=dict(
        t=100
    ),
    hovermode='closest',
    annotations=[
           dict(
           showarrow=False,
            text="Data source: <a href='http://bost.ocks.org/mike/miserables/miserables.json'>[1] miserables.json</a>",
            xref='paper',
            yref='paper',
            x=0,
            y=0.1,
            xanchor='left',
            yanchor='bottom',
            font=dict(
            size=14
            )
            )
        ],    )

In [16]:
plot_data=[trace1, trace2]
fig=go.Figure(data=plot_data, layout=layout)

iplot(fig)

## extra-curricular data exploration

In [28]:
data.keys()

dict_keys(['links', 'nodes'])

In [30]:
data['links'][:10]

[{'source': 1, 'target': 0, 'value': 1},
 {'source': 2, 'target': 0, 'value': 8},
 {'source': 3, 'target': 0, 'value': 10},
 {'source': 3, 'target': 2, 'value': 6},
 {'source': 4, 'target': 0, 'value': 1},
 {'source': 5, 'target': 0, 'value': 1},
 {'source': 6, 'target': 0, 'value': 1},
 {'source': 7, 'target': 0, 'value': 1},
 {'source': 8, 'target': 0, 'value': 2},
 {'source': 9, 'target': 0, 'value': 1}]

In [31]:
data['nodes'][:10]

[{'group': 1, 'name': 'Myriel'},
 {'group': 1, 'name': 'Napoleon'},
 {'group': 1, 'name': 'Mlle.Baptistine'},
 {'group': 1, 'name': 'Mme.Magloire'},
 {'group': 1, 'name': 'CountessdeLo'},
 {'group': 1, 'name': 'Geborand'},
 {'group': 1, 'name': 'Champtercier'},
 {'group': 1, 'name': 'Cravatte'},
 {'group': 1, 'name': 'Count'},
 {'group': 1, 'name': 'OldMan'}]

In [1]:
with open("data/animalia_raw.xml", 'r') as f:
    raw = f.read().split('\n')
print(len(raw))

100001


In [2]:
# parsing...
#little_raw = raw[:10000]
little_raw = raw
#nodes_raw = [n.strip() for n in little_raw if "ID=" in n]
nodes_raw = []
for i in range(len(little_raw)):
    n = little_raw[i]
    try:
        nplus = little_raw[i+1]
    except:
        nplus = "<no next>"
    if "ID=" in n:
        nodes_raw.append(n.strip() + nplus.strip())
print(len(nodes_raw))
n = nodes_raw[0]
print(n)

8007
<NODE EXTINCT="0" ID="2374" CONFIDENCE="0" PHYLESIS="0" LEAF="0" HASPAGE="1" ANCESTORWITHPAGE="3" ITALICIZENAME="0" INCOMPLETESUBGROUPS="0" SHOWAUTHORITY="0" SHOWAUTHORITYCONTAINING="0" IS_NEW_COMBINATION="0" COMBINATION_DATE="null" CHILDCOUNT="2"><NAME><![CDATA[Animals]]></NAME>


In [3]:
def split_stat(n, start, end):
    try:
        this_stat = n.split(start)[1].split(end)[0]
    except:
        this_stat = "no {}".format(start)
    return this_stat

In [4]:
nodes_list = []
for n in nodes_raw:
    # get grouping
    this_group = int(split_stat(n, 'NODE EXTINCT="', '"'))
    # get phylesis
    this_phylesis = int(split_stat(n, 'PHYLESIS="', '"'))
    # get id
    this_id = int(split_stat(n, 'ID="', '"'))
    # get name
    this_name = split_stat(n, 'CDATA[', ']')
    # get num ancestors
    this_ancestor = int(split_stat(n, 'ANCESTORWITHPAGE="', '"'))
    # get num kids
    this_num_kids = int(split_stat(n, 'CHILDCOUNT="', '"'))
    # assign
    nodes_list.append({
        'group' : this_group,
        'phylesis' : this_phylesis,
        'id' : this_id,
        'name' : this_name,
        'ancestor' : this_ancestor,
        'num_kids' : this_num_kids
    })

In [5]:
links_list = []
for n in nodes_list:
    links_list.append({
        'source': n['id'], 
        'target': n['ancestor'], 
        'value': n['num_kids']
    })

In [6]:
import pandas as pd

In [7]:
df = pd.DataFrame(nodes_list)
#df = df.set_index('id')
df.head()

ancestor  group    id           name  num_kids  phylesis
0         3      0  2374        Animals         2         0
1      2374      0  2458      no CDATA[         5         0
2      2374      0  2459      Bilateria        11         0
3      2459      0  2466  Deuterostomia         2         0
4      2466      0  2496      no CDATA[         2         0

In [8]:
e = df['id'][5]
df[df['id'] == e].index.values[0]

5

In [9]:
from collections import Counter

In [10]:
print(Counter(df['phylesis']))
print(Counter(df['group']))

Counter({0: 7916, 1: 57, 2: 34})
Counter({0: 7189, 2: 818})


In [11]:
import numpy as np
from sklearn.decomposition import PCA
pca = PCA(n_components=2)

In [12]:
X = np.matrix(df[['group', 'num_kids', 'ancestor']])

In [13]:
pca.fit(X)

PCA(copy=True, n_components=2, whiten=False)

In [14]:
print(pca.components_)

[[  5.31783559e-06   1.09771379e-05  -1.00000000e+00]
 [  2.90291678e-02  -9.99578565e-01  -1.08181394e-05]]


In [20]:
# plot principal components
X_pca = pca.transform(X)

# Create a trace
trace = go.Scatter(
    x = X_pca[:, 0],
    y = X_pca[:, 1],
    mode = 'markers',
    marker=dict(
        size=16,
        color = np.array(df['ancestor']), #set color equal to a variable
        colorscale='Viridis',
        showscale=True
    )
)

data = [trace]

# Plot and embed in ipython notebook!
#iplot(data, filename='basic-scatter')


In [21]:
depth = len(links_list)
data = {'links' : links_list[:depth], 'nodes' : nodes_list[:depth]}

In [22]:
L=len(data['links'])
Edges=[(data['links'][k]['source'], data['links'][k]['target']) for k in range(L)]

G=ig.Graph(Edges, directed=False)

In [23]:
labels=[]
group=[]
for node in data['nodes']:
    labels.append(node['name'])
    group.append(node['group'])

In [24]:
### custom third dim
layt = []
X_pca = PCA(n_components=2).fit(X).transform(X)
third = 'phylesis'
for i in range(len(X_pca)):
    layt.append(list(X_pca[i]) + [df[third][i]])
print(len(layt))
layt[5]

8007


[58067.690922886213, -2.3668700611964351, 0]

In [25]:
## all 3 PCA
#layt = []
#X_pca = PCA(n_components=3).fit(X).transform(X)
#for i in range(len(X_pca)):
#    layt.append(list(X_pca[i]))
#print(len(layt))
#layt[5]

In [26]:
Xn=[layt[k][0] for k in range(len(layt))]# x-coordinates of nodes
Yn=[layt[k][1] for k in range(len(layt))]# y-coordinates
Zn=[layt[k][2] for k in range(len(layt))]# z-coordinates

In [27]:
Xe=[]
Ye=[]
Ze=[]
for e in Edges:
    try: 
        e0 = df[df['id'] == e[0]].index.values[0]
    except:
        e0 = 0
    try:
        e1 = df[df['id'] == e[1]].index.values[0]
    except:
        e1 = 0
    #
    Xe+=[layt[e0][0],layt[e1][0], None]# x-coordinates of edge ends
    Ye+=[layt[e0][1],layt[e1][1], None]  
    Ze+=[layt[e0][2],layt[e1][2], None] 


## plotly

In [28]:
this_title = ""
this_text = ""

#
trace1=go.Scatter3d(x=Xe,
               y=Ye,
               z=Ze,
               mode='lines',
               line=dict(color='rgb(125,125,125)', width=1),
               hoverinfo='none'
               )

trace2=go.Scatter3d(x=Xn,
               y=Yn,
               z=Zn,
               mode='markers',
               name='actors',
               marker=dict(symbol='circle',
                             size=6,
                             color=group,
                             colorscale='Viridis',
                             line=dict(color='rgb(50,50,50)', width=0.5)
                             ),
               text=labels,
               hoverinfo='text'
               )

axis=dict(showbackground=False,
          showline=False,
          zeroline=False,
          showgrid=False,
          showticklabels=False,
          title=''
          )

layout = go.Layout(
         title=this_title,
         width=1000,
         height=1000,
         showlegend=False,
         scene=dict(
             xaxis=dict(axis),
             yaxis=dict(axis),
             zaxis=dict(axis),
        ),
     margin=dict(
        t=100
    ),
    hovermode='closest',
    annotations=[
           dict(
           showarrow=False,
            text=this_text,
            xref='paper',
            yref='paper',
            x=0,
            y=0.1,
            xanchor='left',
            yanchor='bottom',
            font=dict(
            size=14
            )
            )
        ],    )

In [30]:
plot_data=[trace1, trace2]
fig=go.Figure(data=plot_data, layout=layout)

iplot(fig)

In [ ]:
### coord ideas
# Z = year first seen
# X and Y = lat and long first seen